### Folium

Geospatial library built leaflet.js for Python

In [1]:
import folium
import pandas as pd
import numpy as np

In [2]:
sd_libraries = folium.Map(
    location = [32.7157,-117.1611],
    zoom_start = 10,
    tiles = 'Stamen Terrain')

In [3]:
sd_libraries

In [4]:
folium.GeoJson('data/libraries_datasd.geojson', name = 'geojson').add_to(sd_libraries)
#Alternative way to add markers from geojson file:
#sd_libraries.choropleth('data/libraries_datasd.geojson', line_color='blue')

In [5]:
sd_libraries

Add a Tooltip and Markers

In [6]:
tooltip = 'Click me!'

In [7]:
folium.Marker([32.7167, -117.1661]
              , popup='<i>Downtown San Diego</i>'
              , icon=folium.Icon(color='red', icon='info-sign')).add_to(sd_libraries)

In [8]:
sd_libraries

Let's explore the GeoJson file contents with the GeoPandas library:

In [9]:
import geopandas as gpd

In [10]:
libraries_df = gpd.read_file('data/libraries_datasd.geojson')

In [11]:
parks_df = gpd.read_file('data/parks_datasd.geojson')

In [12]:
print("Shape of Libraries File: ", libraries_df.shape)
print("Shape of Parks File: ", parks_df.shape)

Shape of Libraries File:  (37, 9)
Shape of Parks File:  (2167, 6)


The Parks file is too big and plotting each data point in Folium will cause a data rate failure. Let's reduce the size of the parks dataset and create a modified version of the Parks GeoJson file

In [13]:
parks_df.head()

objectid                          name   gis_acres park_type  \
0       273                   Sunset Park    4.930432     Local   
1       291  Mission Trails Regional Park  451.537474     Local   
2       383                    CALUMET NP    0.727183     Local   
3       384                LINDA VISTA CP   15.880968     Local   
4       385             CANYON HILLS PARK   54.593878  Regional   

                     location  \
0                               
1                               
2  5433 Calumet Avenue, 92037   
3        6842 OSLER ST, 92111   
4     12300 Alemania Rd,92129   

                                            geometry  
0  POLYGON ((-117.03688959 32.78154193, -117.0368...  
1  (POLYGON ((-117.03642396 32.79687307, -117.036...  
2  POLYGON ((-117.26910377 32.81048038, -117.2694...  
3  (POLYGON ((-117.16950697 32.79256687, -117.169...  
4  POLYGON ((-117.1136999 32.93651054, -117.11339...

In [14]:
#picking the top 25 largers parks:
largest_index = parks_df["gis_acres"].nlargest(25).index
new_parks_df = parks_df.loc[largest_index]

In [15]:
import fiona; 
print("Supported file formats to write the file:")
fiona.supported_drivers

Supported file formats to write the file:


{'AeronavFAA': 'r',
 'ARCGEN': 'r',
 'BNA': 'raw',
 'DXF': 'raw',
 'OpenFileGDB': 'r',
 'ESRI Shapefile': 'raw',
 'GeoJSON': 'rw',
 'GPKG': 'rw',
 'GPX': 'raw',
 'GPSTrackMaker': 'raw',
 'Idrisi': 'r',
 'MapInfo File': 'raw',
 'DGN': 'raw',
 'PCIDSK': 'r',
 'SEGY': 'r',
 'SUA': 'r'}

In [17]:
new_parks_df.to_file('data/newparks6.geojson', driver = 'GeoJSON')

In [18]:
#Loading back the file:
new_parks = gpd.read_file('data/newparks3.geojson')

In [19]:
new_parks.shape

(25, 6)

In [20]:
sd_parks = folium.Map(
    location = [32.7157,-117.1611],
    zoom_start = 10
    #,tiles = 'Stamen Toner'
)

In [21]:
folium.GeoJson('data/newparks3.geojson', name = 'geojson').add_to(sd_parks)

In [22]:
sd_parks

In [23]:
#We can add a red circle marker with Popup Window to the map:
folium.Circle(
    radius=100,
    location=[32.7167, -117.1661],
    popup='Downtown',
    color='crimson',
    fill=False,
).add_to(sd_parks)

In [24]:
#Also adding a larger blue circle East of the city
folium.CircleMarker(
    location=[32.7167, -116.5],
    radius=50,
    popup='Laurelhurst Park',
    color='#3186cc',
    fill=True,
    fill_color='#3186cc'
).add_to(sd_parks)

In [25]:
sd_parks

In [26]:
#Layer Control allows to remove layers from map on command
folium.LayerControl().add_to(sd_parks)

In [27]:
sd_parks

In [28]:
#Adding a circle marker on map based on where user clicks:
folium.features.ClickForMarker(popup="This is the new marker!").add_to(sd_parks)

In [29]:
sd_parks

In [30]:
x = np.linspace(0, 2*np.pi, 300)
lats = 32 + np.cos(np.sqrt(x))
lons = -116 + np.sin(np.sqrt(x))
colors = np.sin(5 * x)

In [31]:
#Drawing ColorLine on the Map:

color_line = folium.features.ColorLine(positions = list(zip(lats, lons)),
                          colors = colors,
                          colormap = ['y', 'red', 'orange'],
                        weight = 10)

color_line.add_to(sd_libraries)

In [32]:
sd_libraries

In [33]:
#Adding new colorline to the map:
#Drawing ColorLine on the Map:

x = np.linspace(0, 2*np.pi, 300)
lats = 31 + np.cos(np.sqrt(x))
lons = -115 + np.sin(np.sqrt(x))
colors = np.sin(5 * x)

color_line2 = folium.features.ColorLine(positions = list(zip(lats, lons)),
                          colors = colors,
                          colormap = ['g','b'],
                        weight = 5)

color_line2.add_to(sd_libraries)

In [34]:
sd_libraries

Heatmap

In [35]:
from folium.plugins import HeatMap

In [36]:
#Creating random normally distributed data points to reflect intensity of heatmap
data = (
    np.random.normal(size=(100, 3)) *
    np.array([[1, 1, 1]]) +
    np.array([[34.89, -117.017, 20]])
).tolist()

#data : list of points of the form [lat, lng] or [lat, lng, weight]
#        The points you want to plot.
#        You can also provide a numpy.array of shape (n,2) or (n,3).
#from https://github.com/python-visualization/folium/blob/master/folium/plugins/heat_map.py

In [37]:
#Adding Heatmap above Barstow, CA
HeatMap(data).add_to(sd_libraries)

sd_libraries

Cloropleth Map

In [38]:
df_can = pd.read_excel('https://ibm.box.com/shared/static/lw190pt9zpy5bd1ptyg2aw15awomz9pu.xlsx',
                     sheet_name='Canada by Citizenship',
                     skiprows=range(20),
                     skipfooter=2)

In [39]:
# clean up the dataset to remove unnecessary columns (eg. REG) 
df_can.drop(['AREA','REG','DEV','Type','Coverage'], axis=1, inplace=True)

# let's rename the columns so that they make sense
df_can.rename(columns={'OdName':'Country', 'AreaName':'Continent','RegName':'Region'}, inplace=True)

# for sake of consistency, let's also make all column labels of type string
df_can.columns = list(map(str, df_can.columns))

# add total column
df_can['Total'] = df_can.sum(axis=1)

# years that we will be using in this lesson - useful for plotting later on
years = list(map(str, range(1980, 2014)))
print ('data dimensions:', df_can.shape)

data dimensions: (195, 39)


In [40]:
world_geo = r'data/world-countries.json' # geojson file

# create a plain world map
world_map = folium.Map(location=[0, 0], zoom_start=2, tiles='Mapbox Bright')

In [41]:
# create a numpy array of length 6 and has linear spacing from the minium total immigration to the maximum total immigration
threshold_scale = np.linspace(df_can['Total'].min(),
                              df_can['Total'].max(),
                              6, dtype=int)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list
threshold_scale[-1] = threshold_scale[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

In [42]:
# let Folium determine the scale.
world_map = folium.Map(location=[0, 0], zoom_start=2, tiles='Mapbox Bright')
world_map.choropleth(
    geo_data=world_geo,
    data=df_can,
    columns=['Country', 'Total'],
    key_on='feature.properties.name',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Immigration to Canada',
    reset=True
)
world_map

Cloropleth Map of Italian Regions

We use the italy-regions.json file to draw polygons reflecting Italy's 20 regions (government entities analogous to states in the US)

In [43]:
italy_regions = r'data/italy-regions.json' # geojson file

# create a plain world map
italy = folium.Map(location=[41.87, 12.56], zoom_start=5, tiles='Mapbox Bright')
italy

In [44]:
italy.choropleth(geo_data = italy_regions)
italy

Now we will load a file including education levels for each of Italy's regions. The important aspect is that this file includes a column we can use as key to do a lookup with the json polygon file.
File Source: http://noi-italia.istat.it/index.php?id=3&tx_usercento_centofe%5Bcategoria%5D=5&tx_usercento_centofe%5Bdove%5D=REGIONI&tx_usercento_centofe%5Baction%5D=show&tx_usercento_centofe%5Bcontroller%5D=Categoria&cHash=6d7c4f6c67af8405326ae79076655063

In [45]:
education_df = pd.read_excel('data/istruzione.xls', sheet_name = 'Dati Italia e Regioni')

In [46]:
#we will use the Territorio column as key to draw each region's data:
education_df.head()

Settore                                         Indicatore Modalità  \
0  Istruzione  25-64enni al più con istruzione secondaria inf...  Femmine   
1  Istruzione  25-64enni al più con istruzione secondaria inf...  Femmine   
2  Istruzione  25-64enni al più con istruzione secondaria inf...  Femmine   
3  Istruzione  25-64enni al più con istruzione secondaria inf...  Femmine   
4  Istruzione  25-64enni al più con istruzione secondaria inf...  Femmine   

      Unità di misura                    Territorio  \
0  valori percentuali                      Piemonte   
1  valori percentuali  Valle d'Aosta/Vallée d'Aoste   
2  valori percentuali                       Liguria   
3  valori percentuali                     Lombardia   
4  valori percentuali  Trentino-Alto Adige/Südtirol   

                                      Fonte     2004     2005     2006  \
0  Istat, Rilevazione sulle forze di lavoro  52.1818  49.5045  46.8723   
1  Istat, Rilevazione sulle forze di lavoro  51.6313  51.0956  50.6725   
2  Istat, Rilevazione sulle forze di lavoro  43.7681  41.0501  41.1262   
3  Istat, Rilevazione sulle forze di lavoro  48.4503  46.4993  45.0865   
4  Istat, Rilevazione sulle forze di lavoro  47.7646  46.4058  45.3085   

      2007 ...      2009     2010     2011     2012       2013       2014  \
0  46.3289 ...   43.6404  41.7257  41.0737  40.4998  39.100239  37.743139   
1  48.8866 ...   47.1307  47.6308  46.9633  42.9487  40.125688  39.360091   
2   40.005 ...     34.78  35.8783  35.8357  35.9632  34.876398  33.521228   
3  43.5335 ...   41.8316  40.6828  39.1025   37.548  36.381239  35.636862   
4  43.4556 ...     39.65  38.6533  37.9748   36.867  34.353684  31.160289   

        2015     2016     2017 Note  
0  36.671603  37.4696  36.6963       
1  39.596682  37.8942  36.4992       
2  33.482752  34.2094  32.9976       
3  34.519279   33.981  33.5036       
4  31.243197   31.272  30.0235       

[5 rows x 21 columns]

In [47]:
education_df.Territorio.unique()

array(['Piemonte', "Valle d'Aosta/Vallée d'Aoste", 'Liguria', 'Lombardia',
       'Trentino-Alto Adige/Südtirol', 'Bolzano/Bozen', 'Trento',
       'Veneto', 'Friuli-Venezia Giulia', 'Emilia-Romagna', 'Toscana',
       'Umbria', 'Marche', 'Lazio', 'Abruzzo', 'Molise', 'Campania',
       'Puglia', 'Basilicata', 'Calabria', 'Sicilia', 'Sardegna',
       'Nord-ovest', 'Nord-est', 'Centro', 'Centro-Nord', 'Mezzogiorno',
       'Italia'], dtype=object)

Now reading the Json polygon file in order to check how each region value is spelled in order to make sure they match with the above

In [48]:
import json
from pandas.io.json import json_normalize

In [49]:
file = 'data/italy-regions.json'
with open(file) as train_file:
    dict_train = json.load(train_file)

In [50]:
dict_train.keys()

dict_keys(['type', 'crs', 'features'])

In [51]:
#the actual geographical features are values linked to the "features" dictionary key
json_normalize(dict_train['features']).head()

geometry.coordinates geometry.type  \
0  [[[8.449759643243958, 46.46176402906602], [8.4...       Polygon   
1  [[[7.588571915813589, 45.970750850433724], [7....       Polygon   
2  [[[[10.249298490410025, 46.61838179328392], [1...  MultiPolygon   
3  [[[12.205544261017547, 47.086368287135684], [1...       Polygon   
4  [[[12.505905320166946, 46.678391366799666], [1...       Polygon   

   properties.area  properties.id  properties.length  \
0     2.539410e+10              1       1.236869e+06   
1     3.259041e+09              2       3.111651e+05   
2     2.386270e+10              3       1.411265e+06   
3     1.360802e+10              4       8.005341e+05   
4     1.840550e+10              5       1.057856e+06   

                properties.name     type  
0                      piemonte  Feature  
1                 valle d'aosta  Feature  
2                     lombardia  Feature  
3  trentino-alto adige/sudtirol  Feature  
4                        veneto  Feature

In [52]:
json_features = json_normalize(dict_train['features'])

In [53]:
#Here are the values for the region names from Json
json_features['properties.name'].unique()

array(['piemonte', "valle d'aosta", 'lombardia',
       'trentino-alto adige/sudtirol', 'veneto', 'friuli venezia giulia',
       'liguria', 'emilia-romagna', 'toscana', 'umbria', 'marche',
       'lazio', 'abruzzo', 'molise', 'campania', 'puglia', 'basilicata',
       'calabria', 'sicilia', 'sardegna'], dtype=object)

There are a few discrepancies so we will adjust the region values in the education_df dataframe

In [54]:
education_df.shape

(532, 21)

In [55]:
education_df['Territorio'].value_counts()

Trentino-Alto Adige/Südtirol    19
Umbria                          19
Calabria                        19
Sardegna                        19
Veneto                          19
Molise                          19
Centro                          19
Marche                          19
Liguria                         19
Nord-ovest                      19
Italia                          19
Lombardia                       19
Friuli-Venezia Giulia           19
Trento                          19
Valle d'Aosta/Vallée d'Aoste    19
Sicilia                         19
Bolzano/Bozen                   19
Basilicata                      19
Emilia-Romagna                  19
Puglia                          19
Centro-Nord                     19
Mezzogiorno                     19
Lazio                           19
Nord-est                        19
Piemonte                        19
Abruzzo                         19
Toscana                         19
Campania                        19
Name: Territorio, dt

In [165]:
#The education_df region values include aggregates (e.g. "Nord-Est") so we will first remove those
edu_df = education_df[~education_df['Territorio'].isin(['Centro-Nord',
                                              'Nord-est',
                                              'Nord-ovest',
                                              'Mezzogiorno',# -> "South"
                                              'Centro',
                                              'Italia',
                                              'Bolzano/Bozen', 
                                              'Trento'])]

In [166]:
edu_df['Territorio'].unique()

array(['Piemonte', "Valle d'Aosta/Vallée d'Aoste", 'Liguria', 'Lombardia',
       'Trentino-Alto Adige/Südtirol', 'Veneto', 'Friuli-Venezia Giulia',
       'Emilia-Romagna', 'Toscana', 'Umbria', 'Marche', 'Lazio',
       'Abruzzo', 'Molise', 'Campania', 'Puglia', 'Basilicata',
       'Calabria', 'Sicilia', 'Sardegna'], dtype=object)

Notice rows include partials for Gender, Age - we will only select people with college degrees of ages 30-34:

In [167]:
edu_df = edu_df[edu_df['Indicatore'] == "30-34enni con istruzione universitaria"]
edu_df = edu_df[edu_df['Modalità'] == "Totale"]
print("Check that dataframe includes only 20 rows, each listing total employment: ", edu_df.shape)

Check that dataframe includes only 20 rows, each listing total employment:  (20, 21)


In [168]:
edu_df['Territorio'].unique()

array(['Piemonte', "Valle d'Aosta/Vallée d'Aoste", 'Liguria', 'Lombardia',
       'Trentino-Alto Adige/Südtirol', 'Veneto', 'Friuli-Venezia Giulia',
       'Emilia-Romagna', 'Toscana', 'Umbria', 'Marche', 'Lazio',
       'Abruzzo', 'Molise', 'Campania', 'Puglia', 'Basilicata',
       'Calabria', 'Sicilia', 'Sardegna'], dtype=object)

In [169]:
#Making all regions lower case:
edu_df['Territorio'] = list(map(str.lower, edu_df['Territorio']))

In [170]:
edu_df

Settore                              Indicatore Modalità  \
140  Istruzione  30-34enni con istruzione universitaria   Totale   
141  Istruzione  30-34enni con istruzione universitaria   Totale   
142  Istruzione  30-34enni con istruzione universitaria   Totale   
143  Istruzione  30-34enni con istruzione universitaria   Totale   
144  Istruzione  30-34enni con istruzione universitaria   Totale   
147  Istruzione  30-34enni con istruzione universitaria   Totale   
148  Istruzione  30-34enni con istruzione universitaria   Totale   
149  Istruzione  30-34enni con istruzione universitaria   Totale   
150  Istruzione  30-34enni con istruzione universitaria   Totale   
151  Istruzione  30-34enni con istruzione universitaria   Totale   
152  Istruzione  30-34enni con istruzione universitaria   Totale   
153  Istruzione  30-34enni con istruzione universitaria   Totale   
154  Istruzione  30-34enni con istruzione universitaria   Totale   
155  Istruzione  30-34enni con istruzione universitaria   Totale   
156  Istruzione  30-34enni con istruzione universitaria   Totale   
157  Istruzione  30-34enni con istruzione universitaria   Totale   
158  Istruzione  30-34enni con istruzione universitaria   Totale   
159  Istruzione  30-34enni con istruzione universitaria   Totale   
160  Istruzione  30-34enni con istruzione universitaria   Totale   
161  Istruzione  30-34enni con istruzione universitaria   Totale   

        Unità di misura                    Territorio  \
140  valori percentuali                      piemonte   
141  valori percentuali  valle d'aosta/vallée d'aoste   
142  valori percentuali                       liguria   
143  valori percentuali                     lombardia   
144  valori percentuali  trentino-alto adige/südtirol   
147  valori percentuali                        veneto   
148  valori percentuali         friuli-venezia giulia   
149  valori percentuali                emilia-romagna   
150  valori percentuali                       toscana   
151  valori percentuali                        umbria   
152  valori percentuali                        marche   
153  valori percentuali                         lazio   
154  valori percentuali                       abruzzo   
155  valori percentuali                        molise   
156  valori percentuali                      campania   
157  valori percentuali                        puglia   
158  valori percentuali                    basilicata   
159  valori percentuali                      calabria   
160  valori percentuali                       sicilia   
161  valori percentuali                      sardegna   

                                        Fonte     2004     2005     2006  \
140  Istat, Rilevazione sulle forze di lavoro  15.4143  16.6337  18.0227   
141  Istat, Rilevazione sulle forze di lavoro  12.9586  16.0191  16.0287   
142  Istat, Rilevazione sulle forze di lavoro  17.9528   16.512  21.5175   
143  Istat, Rilevazione sulle forze di lavoro  16.9449   18.684   19.469   
144  Istat, Rilevazione sulle forze di lavoro  13.6223  15.0438  16.7577   
147  Istat, Rilevazione sulle forze di lavoro  14.8981  16.0618  17.1435   
148  Istat, Rilevazione sulle forze di lavoro  16.9891   19.324  22.5133   
149  Istat, Rilevazione sulle forze di lavoro  17.6668  19.9309   19.607   
150  Istat, Rilevazione sulle forze di lavoro  15.6289  18.4851  16.4595   
151  Istat, Rilevazione sulle forze di lavoro  20.6952  20.2055  20.8505   
152  Istat, Rilevazione sulle forze di lavoro  16.0951  19.4236   22.419   
153  Istat, Rilevazione sulle forze di lavoro  21.0474  22.3683  20.9744   
154  Istat, Rilevazione sulle forze di lavoro  16.3055  20.1311  21.8588   
155  Istat, Rilevazione sulle forze di lavoro  17.2901  19.4885  22.3053   
156  Istat, Rilevazione sulle forze di lavoro   12.793  14.3207  13.7977   
157  Istat, Rilevazione sulle forze di lavoro  11.5013  13.1952   14.229   
158  Istat, Rilevazione sulle forze di lavoro  12.8682  14.5049  16.0563   
159  Istat, R

In [173]:
edu_df.loc[edu_df.Territorio == 'trentino-alto adige/südtirol', 'Territorio'] = 'trentino-alto adige/sudtirol'
edu_df.loc[edu_df.Territorio == 'valle d\'aosta/vallée d\'aoste', 'Territorio'] = 'valle d\'aosta'
edu_df.loc[edu_df.Territorio == 'friuli-venezia giulia', 'Territorio'] = 'friuli venezia giulia'

In [174]:
#We will use the 2017 levels 
edu_df

Settore                              Indicatore Modalità  \
140  Istruzione  30-34enni con istruzione universitaria   Totale   
141  Istruzione  30-34enni con istruzione universitaria   Totale   
142  Istruzione  30-34enni con istruzione universitaria   Totale   
143  Istruzione  30-34enni con istruzione universitaria   Totale   
144  Istruzione  30-34enni con istruzione universitaria   Totale   
147  Istruzione  30-34enni con istruzione universitaria   Totale   
148  Istruzione  30-34enni con istruzione universitaria   Totale   
149  Istruzione  30-34enni con istruzione universitaria   Totale   
150  Istruzione  30-34enni con istruzione universitaria   Totale   
151  Istruzione  30-34enni con istruzione universitaria   Totale   
152  Istruzione  30-34enni con istruzione universitaria   Totale   
153  Istruzione  30-34enni con istruzione universitaria   Totale   
154  Istruzione  30-34enni con istruzione universitaria   Totale   
155  Istruzione  30-34enni con istruzione universitaria   Totale   
156  Istruzione  30-34enni con istruzione universitaria   Totale   
157  Istruzione  30-34enni con istruzione universitaria   Totale   
158  Istruzione  30-34enni con istruzione universitaria   Totale   
159  Istruzione  30-34enni con istruzione universitaria   Totale   
160  Istruzione  30-34enni con istruzione universitaria   Totale   
161  Istruzione  30-34enni con istruzione universitaria   Totale   

        Unità di misura                    Territorio  \
140  valori percentuali                      piemonte   
141  valori percentuali                 valle d'aosta   
142  valori percentuali                       liguria   
143  valori percentuali                     lombardia   
144  valori percentuali  trentino-alto adige/sudtirol   
147  valori percentuali                        veneto   
148  valori percentuali         friuli venezia giulia   
149  valori percentuali                emilia-romagna   
150  valori percentuali                       toscana   
151  valori percentuali                        umbria   
152  valori percentuali                        marche   
153  valori percentuali                         lazio   
154  valori percentuali                       abruzzo   
155  valori percentuali                        molise   
156  valori percentuali                      campania   
157  valori percentuali                        puglia   
158  valori percentuali                    basilicata   
159  valori percentuali                      calabria   
160  valori percentuali                       sicilia   
161  valori percentuali                      sardegna   

                                        Fonte     2004     2005     2006  \
140  Istat, Rilevazione sulle forze di lavoro  15.4143  16.6337  18.0227   
141  Istat, Rilevazione sulle forze di lavoro  12.9586  16.0191  16.0287   
142  Istat, Rilevazione sulle forze di lavoro  17.9528   16.512  21.5175   
143  Istat, Rilevazione sulle forze di lavoro  16.9449   18.684   19.469   
144  Istat, Rilevazione sulle forze di lavoro  13.6223  15.0438  16.7577   
147  Istat, Rilevazione sulle forze di lavoro  14.8981  16.0618  17.1435   
148  Istat, Rilevazione sulle forze di lavoro  16.9891   19.324  22.5133   
149  Istat, Rilevazione sulle forze di lavoro  17.6668  19.9309   19.607   
150  Istat, Rilevazione sulle forze di lavoro  15.6289  18.4851  16.4595   
151  Istat, Rilevazione sulle forze di lavoro  20.6952  20.2055  20.8505   
152  Istat, Rilevazione sulle forze di lavoro  16.0951  19.4236   22.419   
153  Istat, Rilevazione sulle forze di lavoro  21.0474  22.3683  20.9744   
154  Istat, Rilevazione sulle forze di lavoro  16.3055  20.1311  21.8588   
155  Istat, Rilevazione sulle forze di lavoro  17.2901  19.4885  22.3053   
156  Istat, Rilevazione sulle forze di lavoro   12.793  14.3207  13.7977   
157  Istat, Rilevazione sulle forze di lavoro  11.5013  13.1952   14.229   
158  Istat, Rilevazione sulle forze di lavoro  12.8682  14.5049  16.0563   
159  Istat, R

Now we can finally create a new choropleth with the education level data. The color intensity of each region will reflect education level

In [190]:
italy_regions = r'data/italy-regions.json' # geojson file

# create a plain world map
italy = folium.Map(location=[41.87, 12.56], 
                   zoom_start=5, 
                   tiles='Mapbox Bright',
                  control_scale = True)

italy.choropleth(geo_data = italy_regions, 
                 data = edu_df, 
                 columns = ['Territorio', '2017'],
                 key_on = 'feature.properties.name',
                 fill_color = 'OrRd', 
                 fill_opacity = 0.4,
                 legend_name = "% of Population")
italy